In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import requests
import ast
import json
import new_token
import os
import matplotlib.pyplot as plt
import seaborn as sns
import imageio
import subprocess
from subprocess import *
import regex as re
import time

from subprocess import Popen, PIPE, STDOUT
from io import StringIO

# file editing imports:
from io import *
from moviepy.video.io.ffmpeg_tools import ffmpeg_extract_subclip
from moviepy.editor import *
from moviepy.audio import *
import assemblyai as aai
#from scipy.io import wavfile
#from faster_whisper import WhisperModel
import ffmpeg
import glob

/opt/anaconda3/lib/python3.9/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


## Obtain access token

In [2]:
t = new_token.token_class()

In [3]:
client_id, client_secret = t.get_info()

In [4]:
access_credentials = t.get_access_credentials()

## Use access token to request server data from twitch -- get 20 most active streams

In [5]:
url = 'https://api.twitch.tv/helix/streams?language=en' # + '?' + 'user_id=123456&type=highlight'
print(url)

https://api.twitch.tv/helix/streams?language=en


In [6]:
r = requests.get(url, headers = access_credentials)
#r.json()['data']
r

<Response [200]>

In [7]:
## get top 20 streamers and put their data into a df
top_20_streamers = json.loads(r.content)['data']

master_data = []
for i in range(len(top_20_streamers)):
    data = []
    for key in top_20_streamers[i].keys():
        data.append(top_20_streamers[i][key])
    master_data.append(data)
        
top_20_df = pd.DataFrame(data = master_data, columns = top_20_streamers[i].keys())

In [8]:
top_20_df.head()

id    user_id user_login  user_name    game_id          game_name  \
0  41999088856   36481935  esl_dota2  ESL_DOTA2      29595             Dota 2   
1  42377023641   50881182  aztecross  Aztecross     497057          Destiny 2   
2  43754029211  207813352   hasanabi   HasanAbi     509658      Just Chatting   
3  43754094827   32454063    simurgh    Simurgh  737987407         Enshrouded   
4  43753812171   51496027  loltyler1  loltyler1      21779  League of Legends   

   type                                              title  viewer_count  \
0  live  LIVE: Aurora vs. OG - DreamLeague Season 22 - ...         32836   
1  live  ✅ DROPS ENABLED [Guardian GAMES ALL STARS] !gs...         19102   
2  live  🚨SUPER TUESDAY🚨KAYA TURNS 1🚨RYAN GRIM AND JERE...         18573   
3  live  #sponsored Enshrouded | Chill VIBES & GOOD Tim...         17397   
4  live  pile up ! OVERLOAD ! NO ! MUST RELEASE !! PROB...         15457   

             started_at language  \
0  2024-03-05T09:00:53Z       en   
1  2024-03-05T15:06:25Z       en   
2  2024-03-05T19:14:12Z       en   
3  2024-03-05T19:24:35Z       en   
4  2024-03-05T18:53:45Z       en   

                                       thumbnail_url tag_ids  \
0  https://static-cdn.jtvnw.net/previews-ttv/live...      []   
1  https://static-cdn.jtvnw.net/previews-ttv/live...      []   
2  https://static-cdn.jtvnw.net/previews-ttv/live...      []   
3  https://static-cdn.jtvnw.net/previews-ttv/live...      []   
4  https://static-cdn.jtvnw.net/previews-ttv/live...      []   

                                                tags  is_mature  
0                                 [Esports, English]      False  
1                            [English, DropsEnabled]      False  
2                    [news, politics, adhd, English]      False  
3  [Chatty, English, Shooter, AdventureGame, Acti...      False  
4                                          [English]      False

## Get videos from top 20 streamers

In [9]:
streamer_id = top_20_df.iloc[0,:]['user_id']
streamer_id

'36481935'

In [10]:
url = 'https://api.twitch.tv/helix/videos?user_id=' + streamer_id

r = requests.get(url, headers = access_credentials)
json.loads(r.content)

{'data': [{'id': '2082159644',
   'stream_id': None,
   'user_id': '36481935',
   'user_login': 'esl_dota2',
   'user_name': 'ESL_DOTA2',
   'title': 'Dota2 - Team Falcons vs Xtreme Gaming - Game 2 - DreamLeague Season 22 - Group Stage 2',
   'description': '',
   'created_at': '2024-03-05T19:32:46Z',
   'published_at': '2024-03-05T19:32:46Z',
   'url': 'https://www.twitch.tv/videos/2082159644',
   'thumbnail_url': 'https://static-cdn.jtvnw.net/cf_vods/d2nvs31859zcd8/e8205afd4e107b9c7ea2_esl_dota2_86363699927_5996414322/thumb/custom-a14da475-1134-47b1-bed8-63c0b7c63663-%{width}x%{height}.jpeg',
   'viewable': 'public',
   'view_count': 3,
   'language': 'en',
   'type': 'highlight',
   'duration': '37m41s',
   'muted_segments': None},
  {'id': '2082077199',
   'stream_id': None,
   'user_id': '36481935',
   'user_login': 'esl_dota2',
   'user_name': 'ESL_DOTA2',
   'title': 'Dota2 - Shopify Rebellion vs Team Spirit - Game 1 - DreamLeague Season 22 - Group Stage 2',
   'description': ''

## Terminal Commands to Download the chat/vods
#### documentation: https://pypi.org/project/chat-downloader/
#### documentation: https://pypi.org/project/twitch-dl/

In [11]:
def run(command, print_output=True):
    '''
    Runs terminal commands using subprocess
    command: list - command to be interpreted by OS
    '''
    
    # grab output filename
    output_fn = ''
    popen = Popen(command, stdout=PIPE, stderr=STDOUT, universal_newlines=True)
    out = StringIO()
    for line in popen.stdout:
        if print_output:
            if '/Users/peter/Twitch' in line:
                output_fn = line
            else:
                print(line, end='')
        else:
            out.write(line)

    
    popen.stdout.close()
    return_code = popen.wait()

    if not return_code == 0:
        raise RuntimeError(
            'The process call "{}" returned with code {}. The return code is not 0, thus an error '
            'occurred.'.format(list(command), return_code))

    stdout_string = out.getvalue()
    out.close()

    return stdout_string, output_fn

In [13]:
# command for downloading twitch vod at specified output location
cmd = ['twitch-dl',
     'download',
     'https://www.twitch.tv/videos/2069606012',
     '-q',
     'source',
     '-w',
     '8',
     '--overwrite',
     '--output',
     '/Users/peter/Twitch/Twitch_VODs/{channel}_{date}_{id}.{format}']
# run command and save fileoutput fiplepath
out = run(cmd)

Looking up video...
Found: *&$^@&*($^#@*&$^*&@#$^j@&$*@#^$&*j$&*@&*$^@&*$^&*($^j&*@!($j@(!*&$^j!&$^ by xQc
Fetching access token...
Fetching playlists...
Fetching playlist...


Downloaded 530/1307 VODs 40% of ~12.9GB       
Downloaded 641/1307 VODs 49% of ~12.8GB       
Downloaded 641/1307 VODs 49% of ~12.8GB at 8.2MB/s ETA 13:35     
Downloaded 641/1307 VODs 49% of ~12.8GB at 21.9MB/s ETA 05:05     
Downloaded 641/1307 VODs 49% of ~12.8GB at 30.8MB/s ETA 03:37     
Downloaded 641/1307 VODs 49% of ~12.8GB at 34.0MB/s ETA 03:16     
Downloaded 641/1307 VODs 49% of ~12.8GB at 36.7MB/s ETA 03:02     
Downloaded 641/1307 VODs 49% of ~12.8GB at 38.9MB/s ETA 02:51     
Downloaded 642/1307 VODs 49% of ~12.8GB at 43.6MB/s ETA 02:32     
Downloaded 642/1307 VODs 49% of ~12.8GB at 43.7MB/s ETA 02:32     
Downloaded 642/1307 VODs 49% of ~12.8GB at 43.9MB/s ETA 02:31     
Downloaded 642/1307 VODs 49% of ~12.8GB at 43.9MB/s ETA 02:31     
Downloaded 642/1307 VODs 49% of ~12.8GB at 43.8MB/s ETA 02:3

In [14]:
# use regex to get exact output filepath
vod_output_fn = re.findall('/Users.*.mkv', out[-1])[0]
vod_output_fn

'/Users/peter/Twitch/Twitch_VODs/xQc_2024-02-21_2069606012.mkv'

In [15]:
# command for downloading twitch vod at specified output location
chat_path = vod_output_fn.replace('mkv','json').replace('Twitch_VODs','Twitch_VODs_Transcript')
print(chat_path)
cmd = ['chat_downloader',
     'https://www.twitch.tv/videos/2069606012',
     '--output',
     chat_path]

run(cmd)

/Users/peter/Twitch/Twitch_VODs_Transcript/xQc_2024-02-21_2069606012.json
[INFO] Site: twitch.tv
[INFO] Retrieving chat for "*&$^@&*($^#@*&$^*&@#$^j@&$*@#^$&*j$&*@&*$^@&*$^&*($^j&*@!($j@(!*&$^j!&$^".
0:07 | (Moments Badge - Tier 2) ZxMRR: PogU LIVE
0:08 | (Prime Gaming) luvtunee: LIVE
0:08 | (Prime Gaming) zoey_lurker22: LET GO
0:08 | (Moments Badge - Tier 1) ㅅㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁ: @nadimz222 BAND
0:09 | (Prime Gaming) zasbu: Pog Pog
0:09 | (Sub Gifter) rarigirlsick: dada
0:09 | (Moments Badge - Tier 1) ㅅㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁ: @nadimz222 BAND 󠀀
0:10 | (Watching without audio) wizWOT: EASRLY OOO
0:10 | (Sub Gifter) rarigirlsick: DADAD
0:11 | (Moments Badge - Tier 1) ㅅㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁ: @nadimz222 BAND
0:11 | (Moments Badge - Tier 5) solutoh: wtf
0:11 | (Moments Badge - Tier 3) thatguyzapp: YOOOOOO OOOO
0:12 | StonedCoconut: LIVE PogU
0:12 | (Moments Badge - Tier 1) ㅅㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁㅁ: @nadimz222 BAND 󠀀
0:12 | (Moments Badge - Tier 2) z6ssbm1: PagMan LIVE
0:12 | (Sub Gifter) rarigirlsick: DADAD 󠀀
0:12 | (Moments Badge

('', '')

## Download Twitch Chat from Channel Clips - Use these chat logs as training data for
## finding clipworthy moments

In [16]:
streamer_ids = list(top_20_df['user_id'])
streamer_ids.append('71092938') # xQc
clip_urls = []
num_clips = 15
for streamer_id in streamer_ids:
    print(streamer_id)
    
    past_brodcast_times = [] # contains vod published datetimes
    url = f'https://api.twitch.tv/helix/videos?user_id={streamer_id}&sort=time&type=archive&first=100'
    r = requests.get(url, headers = access_credentials)
    
    # add vod timestamps to list
    for elem in json.loads(r.content)['data']:
        past_brodcast_times.append(elem['created_at'])

    if len(past_brodcast_times) == 0:
        continue
    # grab newest time stamp out of all the vods
    newest_video = max(past_brodcast_times) 
    

    url = f'https://api.twitch.tv/helix/clips?broadcaster_id={streamer_id}&first={num_clips}&started_at={newest_video}' 
    r = requests.get(url, headers = access_credentials)
    
    # grab top 15 clips that 
    for elem in json.loads(r.content)['data']:
        print(elem['url'])
        clip_urls.append(elem['url'])
    

# download clips' chats
for url in clip_urls:
    temp_url = url.replace('https://clips.twitch.tv/','') # to make the path clean
    chat_path = f'/Users/peter/Twitch/Twitch_VODs_Transcript/Clips/{temp_url}.json'
    
    try:
        cmd = ['chat_downloader',
         url,
         '--output',
         chat_path]

        run(cmd)
    except:
        print('chat not available')   

36481935
https://clips.twitch.tv/MoldyVibrantAlligatorPMSTwin-rMFixTBzPSV7Wbvh
https://clips.twitch.tv/CourageousInspiringMeerkatWOOP-cn3rcfjewkxB9uE4
https://clips.twitch.tv/SmoothDepressedClipsdadBibleThump-0MQ5RQoViUi9l5eu
https://clips.twitch.tv/AnnoyingSnappyVampireOpieOP-G6wY2T03ESEJ2bqk
https://clips.twitch.tv/TenaciousTransparentHorseGingerPower-gxT_i8Avi4ZwfjS1
https://clips.twitch.tv/DeliciousSmokyClipsmomGrammarKing-xELAx3t65XgHNb3s
https://clips.twitch.tv/RacyMoldyCougarKappaRoss-9x6UaqSIQEEMWWyh
https://clips.twitch.tv/BoxyMoistPorpoiseSaltBae-VMI0Gv-cLTVc6lvA
https://clips.twitch.tv/StormyTriumphantCarrotShazBotstix-djYhsyoTFMXHjT8S
50881182
https://clips.twitch.tv/MagnificentPeacefulLatteUWot-98iWRn_9y1sVMQxm
https://clips.twitch.tv/CallousToughTardigradeBatChest-l2WhCZ6c60NEoyQW
https://clips.twitch.tv/PowerfulSpoopyPeanutBIRB-l71Ygn-1XzykzPtQ
https://clips.twitch.tv/SaltySparklingFalconCharlieBitMe-loBY0651Ck170mW1
https://clips.twitch.tv/MotionlessAgitatedIguanaDorito

In [17]:
def clean_author_id(x):
    try:
        return x['id']
    except:
        return np.NaN
     
        
master_chat = pd.DataFrame()
for clip_url in glob.glob('/Users/peter/Twitch/Twitch_VODs_Transcript/Clips/*'):
    chat = pd.read_json(clip_url)
    chat['author_id'] = chat['author'].apply(lambda x: clean_author_id(x))
    #a = chat.shape[0]
    chat = chat.drop_duplicates(subset = ['author_id','message']) # drop spam messages from same user
    #b = chat.shape[0]
    #print('number of dup. messages dropped: ', str(a-b))
    master_chat = pd.concat([master_chat,chat])


master_chat.reset_index(drop = True, inplace = True)
#master_chat['author_id'] = master_chat['author'].apply(lambda x: clean_author_id(x))

print(master_chat.shape)
master_chat.head()

(71206, 9)


author                 message  \
0  {'display_name': 'shovel_knight25', 'id': '422...  another thomas CLASSIC   
1  {'badges': [{'clickAction': 'GET_TURBO', 'clic...              Enough pls   
2  {'badges': [{'clickAction': 'VISIT_URL', 'clic...                   lmfao   
3  {'colour': '#0000FF', 'display_name': 'marlinb...   INCIDENT chance black   
4  {'badges': [{'clickAction': 'VISIT_URL', 'clic...              xdd Thomas   

                             message_id  message_type  time_in_seconds  \
0  3d7464a2-0d27-4f91-a65f-15c3d93e6928  text_message                0   
1  f863c502-7611-41c8-94d3-7f1381dd4f1c  text_message                1   
2  7c12dc74-9994-44aa-b944-4b2d2a13a8dd  text_message                1   
3  d891d979-c0e5-42a3-9931-6334dabe3622  text_message                2   
4  fade0f8a-1e4c-4982-a5ad-6c32cba7a6e7  text_message                2   

  time_text               timestamp emotes  author_id  
0      0:00 2024-03-05 04:17:06.980    NaN  422869951  
1      0:01 2024-03-05 04:17:07.862    NaN   35079338  
2      0:01 2024-03-05 04:17:08.698    NaN  668472199  
3      0:02 2024-03-05 04:17:09.090    NaN  173134572  
4      0:02 2024-03-05 04:17:09.235    NaN   60749052

In [18]:
# grab all occurrences of messages that occur more than 5 times in the clips
counts = master_chat['message'].value_counts() 
valids = counts[counts>=5].index
keyword_freq = master_chat[master_chat['message'].isin(valids)]['message'].value_counts(
    normalize = True).reset_index().rename(columns = {'message':'freq','index':'message'})
keyword_freq

message      freq
0                KEKW  0.074254
1            OMEGALUL  0.031354
2                 LUL  0.024970
3                 HUH  0.019119
4                LMAO  0.015333
...               ...       ...
1095  ???????????????  0.000156
1096             yipe  0.000156
1097             cold  0.000156
1098             COLD  0.000156
1099             sumX  0.000156

[1100 rows x 2 columns]

In [19]:
keyword_freq[keyword_freq['message'] == 'AINTNOWAY'].iloc[0,1]

0.014049690218411666

## Reading Downloaded VOD Chat

In [20]:
chat_path = vod_output_fn.replace('mkv','json').replace('Twitch_VODs','Twitch_VODs_Transcript')

In [21]:
chat = pd.read_json(chat_path)
chat

author           message  \
0       {'badges': [{'clickAction': None, 'clickURL': ...         PogU LIVE   
1       {'badges': [{'clickAction': 'VISIT_URL', 'clic...              LIVE   
2       {'badges': [{'clickAction': 'VISIT_URL', 'clic...            LET GO   
3       {'badges': [{'clickAction': None, 'clickURL': ...   @nadimz222 BAND   
4       {'badges': [{'clickAction': 'VISIT_URL', 'clic...           Pog Pog   
...                                                   ...               ...   
107143  {'badges': [{'clickAction': None, 'clickURL': ...  KICK IS DOWN omE   
107144  {'badges': [{'clickAction': None, 'clickURL': ...               404   
107145  {'badges': [{'clickAction': None, 'clickURL': ...      KICK IS DOWN   
107146  {'badges': [{'clickAction': None, 'clickURL': ...   404 error Aware   
107147  {'badges': [{'clickAction': None, 'clickURL': ...            Link ?   

                                  message_id  message_type  time_in_seconds  \
0       cab28d13-f851-4844-a0bb-27a1f5d54a2e  text_message                7   
1       1c1bac51-ed7d-472e-8cb0-82dd96d9a0e4  text_message                8   
2       6c1c5058-0206-4f77-bd2e-1fa9404bdf05  text_message                8   
3       e9047586-ce73-4651-990f-e404edbb6b5a  text_message                8   
4       d81a3ca4-f45d-4569-8901-1fdeefbafaef  text_message                9   
...                                      ...           ...              ...   
107143  ba1a27dd-2cc2-45b5-9771-1af748e0726e  text_message            13075   
107144  56146a63-6967-4aad-ace7-23eb0857ba09  text_message            13075   
107145  bc3efcee-7a6a-45f2-9539-7664281219d1  text_message            13075   
107146  02c5361f-7844-4000-ae0d-35b37c42d734  text_message            13075   
107147  dfbe4e71-51ad-4946-b3f3-731bc8084b47  text_message            13075   

       time_text               timestamp emotes  
0           0:07 2024-02-22 03:11:18.646    NaN  
1           0:08 2024-02-22 03:11:18.906    NaN  
2           0:08 2024-02-22 03:11:19.286    NaN  
3           0:08 2024-02-22 03:11:19.535    NaN  
4           0:09 2024-02-22 03:11:20.139    NaN  
...          ...                     ...    ...  
107143   3:37:55 2024-02-22 06:49:05.895    NaN  
107144   3:37:55 2024-02-22 06:49:05.964    NaN  
107145   3:37:55 2024-02-22 06:49:06.065    NaN  
107146   3:37:55 2024-02-22 06:49:06.606    NaN  
107147   3:37:55 2024-02-22 06:49:06.692    NaN  

[107148 rows x 8 columns]

In [22]:
## calculate jaccard similarity score
def jaccard_similarity(s1, s2):
    # intersection of two sets
    intersection = len(pd.Series(list(set(s1).intersection(set(s2)))))
    # Unions of two sets
    union = len(pd.Series(list(set(s1).union(set(s2)))))
    #print(intersection)
    #print(union)
    
    return intersection / union

#jaccard_similarity(chat['message'], master_chat['message'])

## Method for determining which times to clip in vods
#### 1) Generate weighted corpus based on chat from human created clips
#### 2) Give score to every 30 second window in the stream
#### 3) Grab windows w/ scores over certain threshold

In [23]:
def find_clip_duration(chat_df, keyword_freq):
    '''
    Gives timestamps for start and end duration of Twitch VOD clip.
    
    chat_df: pd.DataFarme - df containing twitch chat
    
    returns: list - contains tuples of form (start_time, end_time)
    '''
#     timestamps = []
    
#     #temp_df = chat_df[(chat_df['message'] == 'omE') | (chat_df['message'] == 'omE5')]
#     #temp_df.reset_index(drop = True, inplace = True)
    
    
#     # if there are more comments than there are seconds, make clip
#     i = 0
#     CLIP_DURATION = 30 # MAGIC NUM
#     #NUM_COMMENTS_THRESH  = 15 # num comments that qualify for a timestamp
    
#     for idx, value in chat_df.time_in_seconds.iteritems():
        
        
#         if len(chat_df) - idx <= CLIP_DURATION: # if we try to generate too short of clips at the end, then return
#             print('Number of timestamps: ', i)
#             return timestamps
        
#         target_val = value + CLIP_DURATION

#         #print(idx)
#         #print(value)
#         #print(target_val)

#         window = chat_df[(chat_df['time_in_seconds'] >= idx) & (chat_df['time_in_seconds'] <= idx + CLIP_DURATION)]
#         score = jaccard_similarity(window['message'], master_chat['message'])
#         #if temp_df.time_in_seconds[idx + CLIP_DURATION] <= target_val:
#         print(score)
#         if score >= 0.02:
#             i += 1
#             timestamps.append((value, target_val))
    
    
        
#     print('Number of timestamps: ', i)
#     return timestamps

    CLIP_DURATION = 30 # MAGIC NUM
    SCORE_THRESH = 2.0 # MAGIC NUM
    
    scores = []
    timestamps = []
    min_time = min(chat['time_in_seconds'])
    max_time = max(chat['time_in_seconds'])
    total_time = max_time - min_time
    windows = total_time // CLIP_DURATION # num windows to loop through
    
    # loop through time windows, calculate score based on how well chat lines up w/ human-generated clips, and 
    # return timestamps if score >= SCORE_THRESH
    for window in range(windows):
        score = 0
        temp_df = chat[(chat['time_in_seconds'] >= (CLIP_DURATION * window)) & \
                        (chat['time_in_seconds'] < (CLIP_DURATION * (window + 1)))]
        for idx, elem in temp_df.iterrows():
            if elem['message'] in list(keyword_freq.message.values): # check if chat message is in keyword freq
                freq_score = keyword_freq[keyword_freq['message'] == elem['message']].iloc[0,1]
                score += freq_score
        if score >= SCORE_THRESH:      
            scores.append(score)
            timestamps.append((CLIP_DURATION * window, CLIP_DURATION * (window + 1)))
    
    return timestamps

In [24]:
clip_durations = find_clip_duration(chat, keyword_freq)
clip_durations

[(2760, 2790), (6990, 7020), (7500, 7530)]

## CLIP PIPELINE - HELPER FUNCTIONS

In [25]:
# clip vod
def clip_twitch(twitch_vod, start_time, end_time):
    '''
    clips twitch vod at given times
    
    twitch_vod: str - fp of downloaded twitch vod
    start_time: int - start time (total num seconds) to start clip at
    end_time: int - end time (total num seconds) to end clip at
    
    returns: str - fp of clipped .mp4 twich vod
    '''
    CLIP_PATH = twitch_vod.replace('Twitch_VODs','Twitch_Clips').replace('mkv','mp4')
    
    ffmpeg_extract_subclip(twitch_vod,
                           start_time, 
                           end_time, 
                           targetname=CLIP_PATH)
    
    return CLIP_PATH

In [26]:
# clip GTA vid
def clip_GTA(gta_vod, duration):
    '''
    clips GTA car video for (duration) number of seconds
    
    gta_vod: str - fp of downloaded GTA vod
    duration: int - num seconds of GTA clip 
    
    returns: GTA_PATH (str) - fp of clipped GTA vod
    '''
    # use command line to download from youtube in python
    #!yt-dlp "https://www.youtube.com/watch?v=OoP7csWPmWo&ab_channel=DopeGameplays" -o /Users/peter/Twitch/GTA_Gameplay/GTA_test.mkv
    
    
    OFFSET = 10 # magic num, skips first 10 seconds of video
    GTA_PATH = "/Users/peter/Twitch/GTA_Gameplay/GTA_test_clip.mp4" # output fp
    
    ffmpeg_extract_subclip(gta_vod,
                           OFFSET, 
                           duration + OFFSET, 
                           targetname=GTA_PATH)
    
    return GTA_PATH
    

In [27]:
# stack clips
def stack_clips(CLIP_PATH, GTA_PATH):
    '''
    stacks clips, one on top of the other
    CLIP_PATH: str -  fp of twitch clip
    GTA_PATH: str - fp of GTA car clip
    
    returns: STACKED_PATH (str) - fp of stacked clip
    
    '''
    # where to send stacked version of clip
    STACKED_PATH = vod_output_fn.replace('Twitch_VODs','Twitch_Stacked_Clips').replace('mkv','mp4')

    # STREAM CLIP
    clip1 = VideoFileClip(CLIP_PATH)
    # GTA CLIP
    clip2 = VideoFileClip(GTA_PATH)
    # set GTA volume to 0 
    clip2 = clip2.volumex(0)

    # resize clips and adjust to make same size
    c1_height = clip1.size[1]
    c1_width = clip1.size[0]

    c2_height = clip2.size[1]
    c2_width = clip2.size[0]

    min_height = min(c1_height, c2_height)
    min_width = min(c1_width, c2_width)

    clip1 = clip1.resize(width = min_width, height = min_height)
    clip2 = clip2.resize(width = min_width, height = min_height)

    assert(clip1.size == clip2.size)

    clips = [[clip1], [clip2]]

    final = clips_array(clips)

    # write to file
    final.write_videofile(STACKED_PATH, codec = 'libx264')
    
    return STACKED_PATH

In [28]:
# generate subtitles
def generate_transcript(transcriber, input_fp):
    '''
    Generates subtitle file.
    
    transriber: Trascriber object from assembly ai
    input_fp: str - fp of .mp4/.mkv file
    
    returns: str - output fp of .srt subtitle file
    '''
    
    transcript = transcriber.transcribe(input_fp)
    
    SUB_PATH = vod_output_fn.replace('Twitch_VODs','Twitch_VODs_Transcript').replace('.mp4','.srt')
    
    MAX_CHAR = max([len(x) for x in transcript.text.split()])
    srt = transcript.export_subtitles_srt(chars_per_caption=MAX_CHAR)

    # Save it to a file
    with open(SUB_PATH, "w") as f:
        f.write(srt)
        
    return SUB_PATH

In [29]:
# https://www.bannerbear.com/blog/how-to-add-subtitles-to-a-video-with-ffmpeg-5-different-styles/#:~:text=for%20its%20text.-,How%20to%20Change%20the%20Subtitle%20Style,a%20Video%20File%20Using%20FFmpeg
fontstyles = [     
    'Fontname=Trebuchet MS', # anime style
    'Fontname=Roboto,OutlineColour=&H40000000,BorderStyle=3' #  youtube style
    'Fontname=Consolas,BackColour=&H80000000,Spacing=0.2,Outline=0,Shadow=0.75' # netflix style
    'PrimaryColour=&H03fcff,Italic=1,Spacing=0.8' # vintage yellow style
]

font_locs = [
    'Alignment=1', # bottom right
    'Alignment=2', # bottom middle
    'Alignment=3', # bottom left
    'Alignment=4', # top left
    'Alignment=6', # top middle 
    'Alignment=7', # top right
    'Alignment=9', # left middle 
    'Alignment=10', # center
    'Alignment=11', # right middle
]



def add_subtitle_to_video(soft_subtitle, subtitle_file,  subtitle_language, input_video, output_video_name, 
                          font_style = 'Fontname=Trebuchet MS', font_loc = 'Alignment=10'):

    '''
    Adds subtitle to video
    
    soft_subtitle: Boolean - determines if wants soft subtitles
    subtitle_file: str - subtitle fp, should be a .srt file 
    subtitle_language: str - 'eng' is english
    input_video: str - input video fp
    output_video_name: str - output video fp
    font_style: str - font style
    font_loc: str - location of font
    
    returns: None
    '''
    video_input_stream = ffmpeg.input(input_video)
    subtitle_input_stream = ffmpeg.input(subtitle_file)
    output_video = output_video_name
    subtitle_track_title = subtitle_file.replace(".srt", "")
    

    if soft_subtitle:
        stream = ffmpeg.output(
            video_input_stream, subtitle_input_stream, output_video_name, **{"c": "copy", "c:s": "mov_text"},
            **{"metadata:s:s:0": f"language={subtitle_language}",
            "metadata:s:s:0": f"title={subtitle_track_title}"}
        )
        ffmpeg.run(stream, overwrite_output=True)
    else:
        stream = ffmpeg.output(video_input_stream, output_video_name,
                                
                               vf=f"subtitles={subtitle_file}:force_style='{font_loc},{font_style}'")

        ffmpeg.run(stream, overwrite_output=True)
        
        
    return None

## CLIP PIPELINE

In [30]:
# pipe
def clip_pipeline(twitch_vod, gta_vod, timestamp, output_path, transcriber):
    '''
    Takes vod and clips it using the timestamps given. Will go through the following process:
    1. clip vod using timestamp
    2. clip gta yt vid, matches total duration of timestamp
    3. stacks (1) and (2) together into a single clip, one on top of the other
    4. Generates subtitles for (1)
    5. Adds subtitles to (3), outputs final result
    
    twitch_vod: str - fp of downloaded twitch vod
    gta_vod: str - fp of downloaded gta vod
    timestamp: list of tuples - tuples in the form (start_time, end_time) --> tells us when to clip vod
    output_path: str - output of final result
    
    returns: None
    '''
    
    start_time = timestamp[0]
    end_time = timestamp[1]
    duration = abs(end_time - start_time)
    CLIP_PATH = clip_twitch(twitch_vod, start_time, end_time)
    GTA_PATH = clip_GTA(gta_vod, duration)
    STACKED_PATH = stack_clips(CLIP_PATH, GTA_PATH)
    SUB_PATH = generate_transcript(transcriber, STACKED_PATH)
    
    add_subtitle_to_video(soft_subtitle = False, subtitle_file = SUB_PATH,
                         subtitle_language = 'eng', input_video = STACKED_PATH,
                         output_video_name = output_path,
                         font_style = 'Fontname=Roboto,OutlineColour=&H40000000,BorderStyle=3')
    return None

In [31]:
#https://www.assemblyai.com/docs/speech-to-text/speech-recognition
aai.settings.api_key = "24f3ca78e4474a638696c8fac2cbf55d"
config = aai.TranscriptionConfig(language_detection=True,
                                disfluencies=True,
                             filter_profanity=False)
transcriber = aai.Transcriber(config = config)

In [32]:
# grab clip timestamps
timestamps = find_clip_duration(chat, keyword_freq)
for timestamp in timestamps:
    start = time.time()
    
    # run through pipeline
    clip_pipeline(
        twitch_vod = vod_output_fn,
        gta_vod = "/Users/peter/Twitch/GTA_Gameplay/GTA_test.mkv",
        timestamp = timestamp,
        output_path = vod_output_fn.replace('Twitch_VODs','Twitch_Final_Result').replace('.mkv','_' + str(timestamp) + '.mp4'),
        transcriber = transcriber
    )
    
    end = time.time()
    print(end - start)

Moviepy - Running:
>>> "+ " ".join(cmd)
Moviepy - Command successful
Moviepy - Running:
>>> "+ " ".join(cmd)
Moviepy - Command successful
Moviepy - Building video /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4.
MoviePy - Writing audio in xQc_2024-02-21_2069606012TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4



Moviepy - Done !
Moviepy - video ready /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4


ffmpeg version 4.4.4 Copyright (c) 2000-2023 the FFmpeg developers
  built with Apple clang version 11.0.3 (clang-1103.0.32.62)
  configuration: --prefix=/opt/local --cc=/usr/bin/clang --mandir=/opt/local/share/man --enable-audiotoolbox --disable-indev=jack --disable-libjack --disable-libopencore-amrnb --disable-libopencore-amrwb --disable-libxcb --disable-libxcb-shm --disable-libxcb-xfixes --enable-opencl --disable-outdev=xv --enable-sdl2 --disable-securetransport --enable-videotoolbox --enable-avfilter --enable-avresample --enable-fontconfig --enable-gnutls --enable-libass --enable-libbluray --enable-libdav1d --enable-libfreetype --enable-libfribidi --enable-libmodplug --enable-libmp3lame --enable-libopenjpeg --enable-libopus --enable-librsvg --enable-libsoxr --enable-libspeex --enable-libtheora --enable-libvorbis --enable-libvpx --enable-libzimg --enable-libzvbi --enable-lzma --enable-pthreads --enable-shared --enable-swscale --enable-zlib --enable-libaom --enable-libsvtav1 --arch=x

110.20711207389832
Moviepy - Running:
>>> "+ " ".join(cmd)
Moviepy - Command successful
Moviepy - Running:
>>> "+ " ".join(cmd)
Moviepy - Command successful
Moviepy - Building video /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4.
MoviePy - Writing audio in xQc_2024-02-21_2069606012TEMP_MPY_wvf_snd.mp3


...

MoviePy - Done.
Moviepy - Writing video /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4



Moviepy - Done !
Moviepy - video ready /Users/peter/Twitch/Twitch_Stacked_Clips/xQc_2024-02-21_2069606012.mp4


ffmpeg version 4.4.4 Copyright (c) 2000-2023 the FFmpeg developers
  built with Apple clang version 11.0.3 (clang-1103.0.32.62)
  configuration: --prefix=/opt/local --cc=/usr/bin/clang --mandir=/opt/local/share/man --enable-audiotoolbox --disable-indev=jack --disable-libjack --disable-libopencore-amrnb --disable-libopencore-amrwb --disable-libxcb --disable-libxcb-shm --disable-libxcb-xfixes --enable-opencl --disable-outdev=xv --enable-sdl2 --disable-securetransport --enable-videotoolbox --enable-avfilter --enable-avresample --enable-fontconfig --enable-gnutls --enable-libass --enable-libbluray --enable-libdav1d --enable-libfreetype --enable-libfribidi --enable-libmodplug --enable-libmp3lame --enable-libopenjpeg --enable-libopus --enable-librsvg --enable-libsoxr --enable-libspeex --enable-libtheora --enable-libvorbis --enable-libvpx --enable-libzimg --enable-libzvbi --enable-lzma --enable-pthreads --enable-shared --enable-swscale --enable-zlib --enable-libaom --enable-libsvtav1 --arch=x

109.82298803329468


frame= 1922 fps=117 q=-1.0 Lsize=   14019kB time=00:00:32.02 bitrate=3586.5kbits/s speed=1.95x    
video:13463kB audio:503kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 0.376872%
[libx264 @ 0x7fd8bd025400] frame I:8     Avg QP:18.25  size:137859
[libx264 @ 0x7fd8bd025400] frame P:506   Avg QP:23.06  size: 16153
[libx264 @ 0x7fd8bd025400] frame B:1408  Avg QP:29.56  size:  3203
[libx264 @ 0x7fd8bd025400] consecutive B-frames:  1.2%  2.4%  2.5% 93.9%
[libx264 @ 0x7fd8bd025400] mb I  I16..4: 22.7% 57.2% 20.1%
[libx264 @ 0x7fd8bd025400] mb P  I16..4:  6.7%  9.6%  2.2%  P16..4: 18.4%  3.7%  1.4%  0.0%  0.0%    skip:58.0%
[libx264 @ 0x7fd8bd025400] mb B  I16..4:  0.4%  0.6%  0.3%  B16..8: 11.4%  1.0%  0.1%  direct: 0.4%  skip:85.8%  L0:56.8% L1:39.9% BI: 3.4%
[libx264 @ 0x7fd8bd025400] 8x8 transform intra:51.4% inter:75.1%
[libx264 @ 0x7fd8bd025400] coded y,uvDC,uvAC intra: 34.3% 37.6% 8.2% inter: 2.7% 4.0% 0.4%
[libx264 @ 0x7fd8bd025400] i16 v,h,dc,p: 17% 52% 13% 18%


In [33]:
break

SyntaxError: 'break' outside loop (668683560.py, line 1)

## TikTok and Youtube AutoUploaders

In [86]:
import selenium

In [88]:
print(selenium.__version__)

4.18.1


In [117]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
#https://studio.youtube.com
#https://accounts.google.com
link = "https://studio.youtube.com"
link = 'https://youtube.com'
options = webdriver.ChromeOptions()
options.add_argument("--log-level=3")
options.add_argument("user-data-dir=\\Users\\peter\\Library\\Application Support\\Google\\Chrome Beta\\")
options.binary_location = "\\Applications\\Google Chrome Beta.app\\Contents\\MacOS\\Google Chrome Beta"
service = Service(executable_path='/Applications/Google Chrome Beta.app/Contents/MacOS/Google Chrome Beta')

#driver = webdriver.Chrome() #webdriver.Chrv come(service = service)
driver = webdriver.Chrome(service = service, options = options)
#driver = webdriver.Chrome()
driver.get(link)
time.sleep(5)

driver.quit()

KeyboardInterrupt: 

In [76]:
os.chmod('/Users/peter/Anaconda_Shenanigans/Twitch_API/youtube_autoupload_bot_master/chromedriver.exe', 755)

In [71]:
!echo $PATH

/opt/anaconda3/bin:/opt/anaconda3/condabin:/Library/Frameworks/Python.framework/Versions/3.7/bin:/Library/Frameworks/Python.framework/Versions/3.9/bin:/opt/local/bin:/usr/bin:/bin:/opt/local/sbin:/sbin:/Library/Apple/usr/bin


In [104]:
# some_file.py
from youtube_autoupload_bot_master import main
import sys
# caution: path[0] is reserved for script path (or '' in REPL)
#sys.path.insert(1, '/Users/peter/Anaconda_Shenanigans/Twitch_API/youtube_autoupload_bot_master')

#import file
#sys.path.remove('/youtube-autoupload-bot-master')
#import main.py
#sys.path

 IMPORTANT: Put one or more videos in the *videos* folder in the bot directory. Please make sure to name the video files like this --> Ex: vid1.mp4 vid2.mp4 vid3.mp4 etc..
 Press 1 if you want to spam same video or Press 2 if you want to upload multiple videos: 1
 Put the name of the video you want to upload (Ex: vid.mp4 or myshort.mp4 etc..) ---> vid1.mp4
 How many times you want to upload this video ---> 2


WebDriverException: Message: Can not connect to the Service /Applications/Google Chrome Beta.app/Contents/MacOS/Google Chrome Beta


## Download GTA Gameplay from YT and clip it

In [ ]:
#!yt-dlp "https://www.youtube.com/watch?v=OoP7csWPmWo&ab_channel=DopeGameplays" -o /Users/peter/Twitch/GTA_Gameplay/GTA_test.mkv
offset = 10
ffmpeg_extract_subclip("/Users/peter/Twitch/GTA_Gameplay/GTA_test.mkv",
                       offset, 
                       end_time - start_time + offset, 
                       targetname="/Users/peter/Twitch/GTA_Gameplay/GTA_test_clip.mp4")

In [ ]:
# TO DO:
# change subtitle placement to be center of clip

In [ ]:
## go to twitch channel --> videos --> filter by: clips --> train on chat in these clips

## potential model:
# language model: clean data, embed text data into vectors, and use cosine similarity to find word vectors of
# similar sentiment. Use twitch clips as training data, and use the twitch vods as test data?


## bag of words model --> simply calculates the amount of overlap between two documents --> Jaccard similarity
## NGRAM: is able to handle multi-word expressions, which BoW cannot do. Should combine Ngram w BoW together 
## Doc2Vec: represent documents as vectors and use the distance as a similarity measure
## Transformers: also work by representing words and sentences as vectors, but with a crucial difference that the vector representation 
## of a word is not fixed but is itself dependent on the context of the word.
## the state of the art in document similarity and other NLP tasks, but is very computationally expensive
## Term Frequency - Inverse Document Frequency (TF-IDF) is a widely used statistical method in natural 
## language processing and information retrieval. It measures how important a term is within a document 
## relative to a collection of documents (i.e., relative to a corpus).

In [ ]:
# SPLIT NOTEBOOKS:
# twitch api
# download vod and vod chat
# generate timestamps using clip algo & chat
# clip pipeline
# tiktok/yt autouploader